In [1]:
%load_ext autoreload
%autoreload 2

In [15]:
from dataclasses import asdict

import py3Dmol
import torch
import numpy as np
from tqdm import tqdm

from proteome import protein
from proteome.models.design.rfdiffusion import config
from proteome.models.design.rfdiffusion.modeling import RFDiffusionForUnconditionalStructureDesign, RFDiffusionForScaffoldGuidedBinderDesign
from proteome.models.design.rfdiffusion.samplers import SelfConditioning, ScaffoldedSampler
from proteome.models.design.rfdiffusion.util import writepdb

In [3]:
pdb = "1qys.pdb"
with open(pdb, mode="r") as f:
    pdb_str = f.read()
    
input_structure = protein.from_pdb_string(pdb_str, atom14_format=True, parse_hetatom=True)

In [4]:
with open('insulin_target.pdb', mode="r") as f:
    target_pdb_str = f.read()

with open('5L33.pdb', mode="r") as f:
    scaffold_pdb_str = f.read()

In [5]:
def run_sampler(sampler, x_init, seq_init):
    denoised_xyz_stack = []
    px0_xyz_stack = []
    seq_stack = []
    plddt_stack = []
    
    x_t = torch.clone(x_init)
    seq_t = torch.clone(seq_init)
    # Loop over number of reverse diffusion time steps.
    for t in tqdm(range(int(sampler.t_step_input), sampler.inf_conf.final_step - 1, -1)):
        px0, x_t, seq_t, plddt = sampler.sample_step(
            t=t, x_t=x_t, seq_init=seq_t, final_step=sampler.inf_conf.final_step
        )
        px0_xyz_stack.append(px0)
        denoised_xyz_stack.append(x_t)
        seq_stack.append(seq_t)
        plddt_stack.append(plddt[0])

    denoised_xyz_stack = torch.stack(denoised_xyz_stack)
    px0_xyz_stack = torch.stack(px0_xyz_stack)
    plddt_stack = torch.stack(plddt_stack)

    # Save outputs
    final_seq = seq_stack[-1]
    
    # Output glycines, except for motif region
    final_seq = torch.where(
        torch.argmax(seq_init, dim=-1) == 21, 7, torch.argmax(seq_init, dim=-1)
    )  # 7 is glycine
    
    bfacts = torch.ones_like(final_seq.squeeze())
    # make bfact=0 for diffused coordinates
    bfacts[torch.where(torch.argmax(seq_init, dim=-1) == 21, True, False)] = 0

    return protein.Protein(
        atom_positions=denoised_xyz_stack[-1].numpy(),
        aatype=final_seq.numpy(),
        atom_mask=np.ones(denoised_xyz_stack[-1].shape[:2], dtype=np.bool_),
        residue_index=np.arange(1, len(final_seq) + 1, dtype=np.int32),
        b_factors=bfacts[:, None].numpy().repeat(14, axis=-1),
        chain_index=np.array([protein.PDB_CHAIN_IDS.index(char) for char in sampler.chain_idx]),
    )

In [6]:
def show_pdb_string(pdb_str):
    PLDDT_BANDS = [
      (0, 50, '#FF7D45'),
      (50, 70, '#FFDB13'),
      (70, 90, '#65CBF3'),
      (90, 100, '#0053D6')
    ]
    view = py3Dmol.view(width=800, height=600)
    view.addModelsAsFrames(pdb_str)
    
    color_map = {i: bands[2] for i, bands in enumerate(PLDDT_BANDS)}
    style = {'cartoon': {'colorscheme': {'prop': 'b', 'map': color_map}}}
    
    style['stick'] = {}
    
    view.setStyle({'model': -1}, style)
    view.zoomTo()
    return view

## Design cyclic oligos

```bash
../scripts/run_inference.py --config-name=symmetry 
inference.symmetry="C6" 
inference.num_designs=10 
inference.output_prefix="example_outputs/C6_oligo" 
'potentials.guiding_potentials=["type:olig_contacts,weight_intra:1,weight_inter:0.1"]' 
potentials.olig_intra_all=True 
potentials.olig_inter_all=True 
potentials.guide_scale=2.0 
potentials.guide_decay="quadratic" 
'contigmap.contigs=[480-480]'
```

In [7]:
designer = RFDiffusionForUnconditionalStructureDesign(model_name="base")

In [8]:
sampler = SelfConditioning(
    model=designer.model,
    diffuser_conf=designer.cfg.diffuser,
    preprocess_conf=designer.cfg.preprocess,
    inference_conf=config.InferenceConfig(input_structure=input_structure, num_designs=1),
    contigmap_conf=config.ContigMap(contigs=["90-90"]),
    symmetry_conf=config.SymmetryParams(symmetry="C6"),
    ppi_conf=config.PPIParams(),
    denoiser_conf=config.DenoiserParams(),
    potential_conf=config.PotentialsParams(
        guiding_potentials=["type:olig_contacts,weight_intra:1,weight_inter:0.1"], 
        olig_intra_all=True, 
        olig_inter_all=True, 
        guide_scale=2.0, 
        guide_decay="quadratic",
    ),
)

Successful diffuser __init__


In [9]:
x_init, seq_init = sampler.sample_init()

With this beta schedule (linear schedule, beta_0 = 0.04, beta_T = 0.28), alpha_bar_T = 0.00013696050154976547


In [11]:
designed_structure = run_sampler(sampler, x_init, seq_init)

  0%|                                                               | 0/50 [00:00<?, ?it/s]/home/conradry71/micromamba/envs/proteome/lib/python3.10/site-packages/dgl/backend/pytorch/tensor.py:449: UserWarning: TypedStorage is deprecated. It will be removed in the future and UntypedStorage will be the only storage class. This should only matter to you if you are using storages directly.  To access UntypedStorage directly, use tensor.untyped_storage() instead of tensor.storage()
  assert input.numel() == input.storage().size(), (
100%|██████████████████████████████████████████████████████| 50/50 [00:42<00:00,  1.17it/s]


In [12]:
designed_pdb_str = protein.to_pdb(designed_structure)

In [25]:
show_pdb_string(designed_pdb_str)

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

## Dihedral oligos

```bash
python ../scripts/run_inference.py 
--config-name=symmetry 
inference.symmetry="D2" 
inference.num_designs=10 
inference.output_prefix="example_outputs/D2_oligo" 
'potentials.guiding_potentials=["type:olig_contacts,weight_intra:1,weight_inter:0.1"]' 
potentials.olig_intra_all=True 
potentials.olig_inter_all=True 
potentials.guide_scale=2.0 
potentials.guide_decay="quadratic" 
'contigmap.contigs=[320-320]'
```

In [14]:
designer = RFDiffusionForUnconditionalStructureDesign(model_name="base")

In [17]:
sampler = SelfConditioning(
    model=designer.model,
    diffuser_conf=designer.cfg.diffuser,
    preprocess_conf=designer.cfg.preprocess,
    inference_conf=config.InferenceConfig(input_structure=input_structure, num_designs=1),
    contigmap_conf=config.ContigMap(contigs=["120-120"]),
    symmetry_conf=config.SymmetryParams(symmetry="D2"),
    ppi_conf=config.PPIParams(),
    denoiser_conf=config.DenoiserParams(),
    potential_conf=config.PotentialsParams(
        guiding_potentials=["type:olig_contacts,weight_intra:1,weight_inter:0.1"], 
        olig_intra_all=True, 
        olig_inter_all=True, 
        guide_scale=2.0, 
        guide_decay="quadratic",
    ),
)

Successful diffuser __init__


In [18]:
x_init, seq_init = sampler.sample_init()

With this beta schedule (linear schedule, beta_0 = 0.04, beta_T = 0.28), alpha_bar_T = 0.00013696050154976547


In [19]:
designed_structure = run_sampler(sampler, x_init, seq_init)

100%|██████████████████████████████████████████████████████| 50/50 [00:41<00:00,  1.20it/s]


In [20]:
designed_pdb_str = protein.to_pdb(designed_structure)

In [26]:
show_pdb_string(designed_pdb_str)

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

## Enzyme

```bash
../scripts/run_inference.py 
inference.output_prefix=example_outputs/design_enzyme 
inference.input_pdb=input_pdbs/5an7.pdb 
'contigmap.contigs=[10-100/A1083-1083/10-100/A1051-1051/10-100/A1180-1180/10-100]' 
potentials.guide_scale=1 
'potentials.guiding_potentials=["type:substrate_contacts,s:1,r_0:8,rep_r_0:5.0,rep_s:2,rep_r_min:1"]' 
potentials.substrate=LLK 
inference.ckpt_override_path=../models/ActiveSite_ckpt.pt
```

In [30]:
designer = RFDiffusionForUnconditionalStructureDesign(model_name="active_site")

Downloading: "http://files.ipd.uw.edu/pub/RFdiffusion/5532d2e1f3a4738decd58b19d633b3c3/ActiveSite_ckpt.pt" to /home/conradry71/.cache/torch/hub/checkpoints/active_site.pt
100%|███████████████████████████████████████████████████| 461M/461M [00:07<00:00, 64.6MB/s]


In [29]:
with open("5an7.pdb", mode="r") as f:
    pdb_str = f.read()
    
input_structure = protein.from_pdb_string(pdb_str, atom14_format=True, parse_hetatom=True)

In [42]:
sampler = SelfConditioning(
    model=designer.model,
    diffuser_conf=designer.cfg.diffuser,
    preprocess_conf=designer.cfg.preprocess,
    inference_conf=config.InferenceConfig(input_structure=input_structure, num_designs=1),
    contigmap_conf=config.ContigMap(contigs=["10-100/A1083-1083/10-100/A1051-1051/10-100/A1180-1180/10-100"]),
    symmetry_conf=config.SymmetryParams(),
    ppi_conf=config.PPIParams(),
    denoiser_conf=config.DenoiserParams(),
    potential_conf=config.PotentialsParams(
        guiding_potentials=["type:substrate_contacts,s:1,r_0:8,rep_r_0:5.0,rep_s:2,rep_r_min:1"], 
        guide_scale=1, 
        guide_decay="quadratic",
        substrate="LLK",
    ),
)

Successful diffuser __init__


In [43]:
x_init, seq_init = sampler.sample_init()

With this beta schedule (linear schedule, beta_0 = 0.04, beta_T = 0.28), alpha_bar_T = 0.00013696050154976547


In [44]:
designed_structure = run_sampler(sampler, x_init, seq_init)

  2%|█                                                      | 1/50 [00:02<02:17,  2.81s/it]

types torch.float64 torch.float64 torch.float64


  4%|██▏                                                    | 2/50 [00:05<02:10,  2.71s/it]

types torch.float64 torch.float64 torch.float64


  6%|███▎                                                   | 3/50 [00:08<02:06,  2.70s/it]

...

 96%|███████████████████████████████████████████████████▊  | 48/50 [02:07<00:05,  2.64s/it]

types torch.float64 torch.float64 torch.float64


 98%|████████████████████████████████████████████████████▉ | 49/50 [02:09<00:02,  2.64s/it]

types torch.float64 torch.float64 torch.float64


100%|██████████████████████████████████████████████████████| 50/50 [02:12<00:00,  2.65s/it]


In [45]:
designed_pdb_str = protein.to_pdb(designed_structure)

In [46]:
show_pdb_string(designed_pdb_str)

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

## Motifscaffolding InpaintSeq

```bash
../scripts/run_inference.py 
inference.output_prefix=example_outputs/design_motifscaffolding_inpaintseq 
inference.input_pdb=input_pdbs/5TPN.pdb 'contigmap.contigs=[10-40/A163-181/10-40]' 
inference.num_designs=10 
'contigmap.inpaint_seq=[A163-168/A170-171/A179]'
```

In [64]:
designer = RFDiffusionForUnconditionalStructureDesign(model_name="inpaint_seq")

In [65]:
with open("5tpn.pdb", mode="r") as f:
    pdb_str = f.read()
    
input_structure = protein.from_pdb_string(pdb_str, atom14_format=True, parse_hetatom=True)

In [66]:
sampler = SelfConditioning(
    model=designer.model,
    diffuser_conf=designer.cfg.diffuser,
    preprocess_conf=designer.cfg.preprocess,
    inference_conf=config.InferenceConfig(input_structure=input_structure, num_designs=1),
    contigmap_conf=config.ContigMap(contigs=["10-40/A163-181/10-40"], inpaint_seq=["A163-168/A170-171/A179"]),
    symmetry_conf=config.SymmetryParams(),
    ppi_conf=config.PPIParams(),
    denoiser_conf=config.DenoiserParams(),
    potential_conf=config.PotentialsParams(),
)

Successful diffuser __init__


In [67]:
x_init, seq_init = sampler.sample_init()

With this beta schedule (linear schedule, beta_0 = 0.04, beta_T = 0.28), alpha_bar_T = 0.00013696050154976547


In [68]:
designed_structure = run_sampler(sampler, x_init, seq_init)

  0%|                                                               | 0/50 [00:00<?, ?it/s]

  2%|█                                                      | 1/50 [00:00<00:33,  1.48it/s]

  4%|██▏                                                    | 2/50 [00:01<00:31,  1.55it/s]

  6%|███▎                                                   | 3/50 [00:01<00:29,  1.58it/s]

  8%|████▍                                                  | 4/50 [00:02<00:29,  1.57it/s]

...

 94%|██████████████████████████████████████████████████▊   | 47/50 [00:29<00:01,  1.59it/s]

 96%|███████████████████████████████████████████████████▊  | 48/50 [00:30<00:01,  1.61it/s]

 98%|████████████████████████████████████████████████████▉ | 49/50 [00:31<00:00,  1.60it/s]

100%|██████████████████████████████████████████████████████| 50/50 [00:31<00:00,  1.57it/s]

Protein shape torch.Size([73, 14, 3])
mask shape (73, 14)
bfacts shape (73, 14)


In [69]:
designed_pdb_str = protein.to_pdb(designed_structure)

In [70]:
show_pdb_string(designed_pdb_str)

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

## MotifScaffoling with Target

```bash
python ../scripts/run_inference.py 
inference.output_prefix=example_outputs/design_motifscaffolding_with_target 
inference.input_pdb=input_pdbs/1YCR.pdb 
'contigmap.contigs=[A25-109/0 0-70/B17-29/0-70]' 
contigmap.length=70-120 
inference.num_designs=10 
inference.ckpt_override_path=../models/Complex_base_ckpt.pt
```

In [73]:
designer = RFDiffusionForUnconditionalStructureDesign(model_name="complex_base")

In [76]:
with open('1ycr.pdb', mode="r") as f:
    pdb_str = f.read()

input_structure = protein.from_pdb_string(pdb_str, atom14_format=True, parse_hetatom=True)

In [77]:
sampler = SelfConditioning(
    model=designer.model,
    diffuser_conf=designer.cfg.diffuser,
    preprocess_conf=designer.cfg.preprocess,
    inference_conf=config.InferenceConfig(input_structure=input_structure, num_designs=1),
    contigmap_conf=config.ContigMap(contigs=["A25-109/0 0-70/B17-29/0-70"], length="70-120"),
    symmetry_conf=config.SymmetryParams(),
    ppi_conf=config.PPIParams(),
    denoiser_conf=config.DenoiserParams(),
    potential_conf=config.PotentialsParams(),
)

Successful diffuser __init__


In [78]:
x_init, seq_init = sampler.sample_init()

With this beta schedule (linear schedule, beta_0 = 0.04, beta_T = 0.28), alpha_bar_T = 0.00013696050154976547


In [79]:
designed_structure = run_sampler(sampler, x_init, seq_init)

  0%|                                                               | 0/50 [00:00<?, ?it/s]

  2%|█                                                      | 1/50 [00:01<01:16,  1.55s/it]

  4%|██▏                                                    | 2/50 [00:03<01:12,  1.51s/it]

  6%|███▎                                                   | 3/50 [00:04<01:10,  1.49s/it]

  8%|████▍                                                  | 4/50 [00:05<01:08,  1.48s/it]

...

 92%|█████████████████████████████████████████████████▋    | 46/50 [01:08<00:05,  1.46s/it]

 94%|██████████████████████████████████████████████████▊   | 47/50 [01:09<00:04,  1.45s/it]

 96%|███████████████████████████████████████████████████▊  | 48/50 [01:11<00:02,  1.45s/it]

 98%|████████████████████████████████████████████████████▉ | 49/50 [01:12<00:01,  1.45s/it]

100%|██████████████████████████████████████████████████████| 50/50 [01:13<00:00,  1.48s/it]


In [80]:
designed_pdb_str = protein.to_pdb(designed_structure)

In [81]:
show_pdb_string(designed_pdb_str)

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

## Motifscaffolding

```bash
../scripts/run_inference.py 
inference.output_prefix=example_outputs/design_motifscaffolding 
inference.input_pdb=input_pdbs/5TPN.pdb 
'contigmap.contigs=[10-40/A163-181/10-40]' 
inference.num_designs=10
```

In [7]:
designer = RFDiffusionForUnconditionalStructureDesign(model_name="complex_base")

In [8]:
with open('5tpn.pdb', mode="r") as f:
    pdb_str = f.read()

input_structure = protein.from_pdb_string(pdb_str, atom14_format=True, parse_hetatom=True)

In [9]:
sampler = SelfConditioning(
    model=designer.model,
    diffuser_conf=designer.cfg.diffuser,
    preprocess_conf=designer.cfg.preprocess,
    inference_conf=config.InferenceConfig(input_structure=input_structure, num_designs=1),
    contigmap_conf=config.ContigMap(contigs=["10-40/A163-181/10-40"]),
    symmetry_conf=config.SymmetryParams(),
    ppi_conf=config.PPIParams(),
    denoiser_conf=config.DenoiserParams(),
    potential_conf=config.PotentialsParams(),
)

Successful diffuser __init__


In [11]:
x_init, seq_init = sampler.sample_init()

With this beta schedule (linear schedule, beta_0 = 0.04, beta_T = 0.28), alpha_bar_T = 0.00013696050154976547


In [12]:
designed_structure = run_sampler(sampler, x_init, seq_init)

  0%|                                                                         | 0/50 [00:00<?, ?it/s]

/home/conradry71/micromamba/envs/proteome/lib/python3.10/site-packages/dgl/backend/pytorch/tensor.py:449: UserWarning: TypedStorage is deprecated. It will be removed in the future and UntypedStorage will be the only storage class. This should only matter to you if you are using storages directly.  To access UntypedStorage directly, use tensor.untyped_storage() instead of tensor.storage()
  assert input.numel() == input.storage().size(), (
  2%|█▎                                                               | 1/50 [00:06<05:03,  6.20s/it]

  4%|██▌                                                              | 2/50 [00:06<02:19,  2.91s/it]

  6%|███▉                                                             | 3/50 [00:07<01:27,  1.86s/it]

  8%|█████▏                                                           | 4/50 [00:08<01:02,  1.37s/it]

...

 92%|██████████████████████████████████████████████████████████▉     | 46/50 [00:33<00:02,  1.66it/s]

 94%|████████████████████████████████████████████████████████████▏   | 47/50 [00:34<00:01,  1.67it/s]

 96%|█████████████████████████████████████████████████████████████▍  | 48/50 [00:34<00:01,  1.67it/s]

 98%|██████████████████████████████████████████████████████████████▋ | 49/50 [00:35<00:00,  1.65it/s]

100%|████████████████████████████████████████████████████████████████| 50/50 [00:36<00:00,  1.39it/s]


In [13]:
designed_pdb_str = protein.to_pdb(designed_structure)

In [14]:
show_pdb_string(designed_pdb_str)

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

## Design nickel

```bash
ckpt='../models/Base_epoch8_ckpt.pt'

python ../scripts/run_inference.py 
inference.symmetry="C4" 
inference.num_designs=15 
inference.output_prefix=example_outputs/design_nickel 
'potentials.guiding_potentials=["type:olig_contacts,weight_intra:1,weight_inter:0.06"]' 
potentials.olig_intra_all=True 
potentials.olig_inter_all=True 
potentials.guide_scale=2 
potentials.guide_decay="quadratic" 
inference.input_pdb=input_pdbs/nickel_symmetric_motif.pdb 
'contigmap.contigs=[50/A2-4/50/0 50/A7-9/50/0 50/A12-14/50/0 50/A17-19/50/0]' 
inference.ckpt_override_path=$ckpt
```

In [7]:
designer = RFDiffusionForUnconditionalStructureDesign(model_name="base_epoch8")

Downloading: "http://files.ipd.uw.edu/pub/RFdiffusion/12fc204edeae5b57713c5ad7dcb97d39/Base_epoch8_ckpt.pt" to /home/conradry71/.cache/torch/hub/checkpoints/base_epoch8.pt
100%|██████████████████████████████████████████████████████| 461M/461M [00:07<00:00, 68.1MB/s]


In [8]:
with open('nickel_motif.pdb', mode="r") as f:
    pdb_str = f.read()

input_structure = protein.from_pdb_string(pdb_str, atom14_format=True, parse_hetatom=True)

In [9]:
sampler = SelfConditioning(
    model=designer.model,
    diffuser_conf=designer.cfg.diffuser,
    preprocess_conf=designer.cfg.preprocess,
    inference_conf=config.InferenceConfig(input_structure=input_structure, num_designs=1),
    contigmap_conf=config.ContigMap(contigs=["50/A2-4/50/0 50/A7-9/50/0 50/A12-14/50/0 50/A17-19/50/0"]),
    symmetry_conf=config.SymmetryParams(symmetry="c4"),
    ppi_conf=config.PPIParams(),
    denoiser_conf=config.DenoiserParams(),
    potential_conf=config.PotentialsParams(
        guiding_potentials=["type:olig_contacts,weight_intra:1,weight_inter:0.06"],
        olig_inter_all=True,
        olig_intra_all=True,
        guide_scale=2,
        guide_decay="quadratic",
    ),
)

Successful diffuser __init__


In [11]:
x_init, seq_init = sampler.sample_init()
designed_structure = run_sampler(sampler, x_init, seq_init)

With this beta schedule (linear schedule, beta_0 = 0.04, beta_T = 0.28), alpha_bar_T = 0.00013696050154976547


  0%|                                                                  | 0/50 [00:00<?, ?it/s]/home/conradry71/micromamba/envs/proteome/lib/python3.10/site-packages/dgl/backend/pytorch/tensor.py:449: UserWarning: TypedStorage is deprecated. It will be removed in the future and UntypedStorage will be the only storage class. This should only matter to you if you are using storages directly.  To access UntypedStorage directly, use tensor.untyped_storage() instead of tensor.storage()
  assert input.numel() == input.storage().size(), (
100%|█████████████████████████████████████████████████████████| 50/50 [07:04<00:00,  8.49s/it]


In [12]:
designed_pdb_str = protein.to_pdb(designed_structure)
show_pdb_string(designed_pdb_str)

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

## Partial Diffusion Multiseq

```bash
../scripts/run_inference.py 
inference.output_prefix=example_outputs/design_partialdiffusion_peptidewithmultiplesequence 
inference.input_pdb=input_pdbs/peptide_complex_ideal_helix.pdb 
'contigmap.contigs=["172-172/0 34-34"]' 
diffuser.partial_T=10 
inference.num_designs=10 
'contigmap.provide_seq=[172-177,200-205]'
```

In [13]:
designer = RFDiffusionForUnconditionalStructureDesign(model_name="inpaint_seq")

In [14]:
with open('peptide_complex.pdb', mode="r") as f:
    pdb_str = f.read()

input_structure = protein.from_pdb_string(pdb_str, atom14_format=True, parse_hetatom=True)

In [17]:
diffuser_default = asdict(designer.cfg.diffuser)
diffuser_default["partial_T"] = 10
diffuser_config = config.DiffuserConfig(**diffuser_default)

In [18]:
sampler = SelfConditioning(
    model=designer.model,
    diffuser_conf=diffuser_config,
    preprocess_conf=designer.cfg.preprocess,
    inference_conf=config.InferenceConfig(input_structure=input_structure, num_designs=1),
    contigmap_conf=config.ContigMap(contigs=["172-172/0 34-34"], provide_seq=["172-177,200-205"]),
    symmetry_conf=config.SymmetryParams(),
    ppi_conf=config.PPIParams(),
    denoiser_conf=config.DenoiserParams(),
    potential_conf=config.PotentialsParams(),
)

Successful diffuser __init__


In [19]:
x_init, seq_init = sampler.sample_init()
designed_structure = run_sampler(sampler, x_init, seq_init)

With this beta schedule (linear schedule, beta_0 = 0.04, beta_T = 0.28), alpha_bar_T = 0.00013696050154976547


  0%|                                                                  | 0/10 [00:00<?, ?it/s]

 10%|█████▊                                                    | 1/10 [00:02<00:18,  2.04s/it]

 20%|███████████▌                                              | 2/10 [00:03<00:15,  1.97s/it]

 30%|█████████████████▍                                        | 3/10 [00:05<00:13,  1.95s/it]

...

 60%|██████████████████████████████████▊                       | 6/10 [00:11<00:07,  1.94s/it]

 70%|████████████████████████████████████████▌                 | 7/10 [00:13<00:05,  1.94s/it]

 80%|██████████████████████████████████████████████▍           | 8/10 [00:15<00:03,  1.94s/it]

 90%|████████████████████████████████████████████████████▏     | 9/10 [00:17<00:01,  1.94s/it]

100%|█████████████████████████████████████████████████████████| 10/10 [00:19<00:00,  1.95s/it]


In [20]:
designed_pdb_str = protein.to_pdb(designed_structure)
show_pdb_string(designed_pdb_str)

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

## Partial Diffusion with Sequence

```bash
../scripts/run_inference.py 
inference.output_prefix=example_outputs/design_partialdiffusion_peptidewithsequence 
inference.input_pdb=input_pdbs/peptide_complex_ideal_helix.pdb 
'contigmap.contigs=["172-172/0 34-34"]' 
diffuser.partial_T=10 
inference.num_designs=10 
'contigmap.provide_seq=[172-205]'
```

In [21]:
designer = RFDiffusionForUnconditionalStructureDesign(model_name="inpaint_seq")

In [22]:
with open('peptide_complex.pdb', mode="r") as f:
    pdb_str = f.read()

input_structure = protein.from_pdb_string(pdb_str, atom14_format=True, parse_hetatom=True)

In [23]:
diffuser_default = asdict(designer.cfg.diffuser)
diffuser_default["partial_T"] = 10
diffuser_config = config.DiffuserConfig(**diffuser_default)

In [24]:
sampler = SelfConditioning(
    model=designer.model,
    diffuser_conf=diffuser_config,
    preprocess_conf=designer.cfg.preprocess,
    inference_conf=config.InferenceConfig(input_structure=input_structure, num_designs=1),
    contigmap_conf=config.ContigMap(contigs=["172-172/0 34-34"], provide_seq=["172-205"]),
    symmetry_conf=config.SymmetryParams(),
    ppi_conf=config.PPIParams(),
    denoiser_conf=config.DenoiserParams(),
    potential_conf=config.PotentialsParams(),
)

Successful diffuser __init__


In [25]:
x_init, seq_init = sampler.sample_init()
designed_structure = run_sampler(sampler, x_init, seq_init)

With this beta schedule (linear schedule, beta_0 = 0.04, beta_T = 0.28), alpha_bar_T = 0.00013696050154976547


  0%|                                                                  | 0/10 [00:00<?, ?it/s]

 10%|█████▊                                                    | 1/10 [00:02<00:18,  2.01s/it]

 20%|███████████▌                                              | 2/10 [00:03<00:15,  1.97s/it]

 30%|█████████████████▍                                        | 3/10 [00:05<00:13,  1.95s/it]

...

 60%|██████████████████████████████████▊                       | 6/10 [00:11<00:07,  1.94s/it]

 70%|████████████████████████████████████████▌                 | 7/10 [00:13<00:05,  1.94s/it]

 80%|██████████████████████████████████████████████▍           | 8/10 [00:15<00:03,  1.94s/it]

 90%|████████████████████████████████████████████████████▏     | 9/10 [00:17<00:01,  1.94s/it]

100%|█████████████████████████████████████████████████████████| 10/10 [00:19<00:00,  1.95s/it]


In [26]:
designed_pdb_str = protein.to_pdb(designed_structure)
show_pdb_string(designed_pdb_str)

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

## Partial Diffusion

```bash
../scripts/run_inference.py 
inference.output_prefix=example_outputs/design_partialdiffusion 
inference.input_pdb=input_pdbs/2KL8.pdb 
'contigmap.contigs=[79-79]' 
inference.num_designs=10 
diffuser.partial_T=10
```

In [27]:
designer = RFDiffusionForUnconditionalStructureDesign(model_name="inpaint_seq")

In [29]:
with open('2kl8.pdb', mode="r") as f:
    pdb_str = f.read()

input_structure = protein.from_pdb_string(pdb_str, atom14_format=True, parse_hetatom=True)

In [30]:
diffuser_default = asdict(designer.cfg.diffuser)
diffuser_default["partial_T"] = 10
diffuser_config = config.DiffuserConfig(**diffuser_default)

In [31]:
sampler = SelfConditioning(
    model=designer.model,
    diffuser_conf=diffuser_config,
    preprocess_conf=designer.cfg.preprocess,
    inference_conf=config.InferenceConfig(input_structure=input_structure, num_designs=1),
    contigmap_conf=config.ContigMap(contigs=["79"]),
    symmetry_conf=config.SymmetryParams(),
    ppi_conf=config.PPIParams(),
    denoiser_conf=config.DenoiserParams(),
    potential_conf=config.PotentialsParams(),
)

Successful diffuser __init__


In [32]:
x_init, seq_init = sampler.sample_init()
designed_structure = run_sampler(sampler, x_init, seq_init)

With this beta schedule (linear schedule, beta_0 = 0.04, beta_T = 0.28), alpha_bar_T = 0.00013696050154976547


100%|█████████████████████████████████████████████████████████| 10/10 [00:06<00:00,  1.61it/s]


In [33]:
designed_pdb_str = protein.to_pdb(designed_structure)
show_pdb_string(designed_pdb_str)

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

## PPI Scaffolded

```bash
../scripts/run_inference.py 
scaffoldguided.target_path=input_pdbs/insulin_target.pdb 
inference.output_prefix=example_outputs/design_ppi_scaffolded 
scaffoldguided.scaffoldguided=True 
'ppi.hotspot_res=[A59,A83,A91]' 
scaffoldguided.target_pdb=True 
scaffoldguided.target_ss=target_folds/insulin_target_ss.pt 
scaffoldguided.target_adj=target_folds/insulin_target_adj.pt 
scaffoldguided.scaffold_dir=./ppi_scaffolds/ 
inference.num_designs=10 
denoiser.noise_scale_ca=0 
denoiser.noise_scale_frame=0
```

In [66]:
designer = RFDiffusionForUnconditionalStructureDesign(model_name="complex_fold_base")

In [67]:
with open('1qys.pdb', mode="r") as f:
    pdb_str = f.read()
input_structure = protein.from_pdb_string(pdb_str, atom14_format=True, parse_hetatom=True)

with open('insulin_target.pdb', mode="r") as f:
    target_pdb_str = f.read()

with open('5L33.pdb', mode="r") as f:
    scaffold_pdb_str = f.read()

In [68]:
sampler = ScaffoldedSampler(
    model=designer.model,
    diffuser_conf=designer.cfg.diffuser,
    preprocess_conf=designer.cfg.preprocess,
    inference_conf=config.InferenceConfig(input_structure=input_structure, num_designs=1),
    contigmap_conf=config.ContigMap(),
    symmetry_conf=config.SymmetryParams(),
    ppi_conf=config.PPIParams(hotspot_res=["A59", "A83", "A91"]),
    denoiser_conf=config.DenoiserParams(noise_scale_ca=0, noise_scale_frame=0),
    potential_conf=config.PotentialsParams(),
    scaffold_conf=config.ScaffoldGuidedParams(
        scaffoldguided=True, target_pdb_str=target_pdb_str, scaffold_pdb_str_list=[scaffold_pdb_str], target_ss=True, target_adj=True
    ),
)

Successful diffuser __init__
core.io.pose_from_sfr.PoseFromSFRBuilder: [ WARNING ] discarding 3 atoms at position 1 in file . Best match rsd_type:  GLU:NtermProteinFull
core.io.pose_from_sfr.PoseFromSFRBuilder: [ WARNING ] discarding 1 atoms at position 2 in file . Best match rsd_type:  VAL
core.io.pose_from_sfr.PoseFromSFRBuilder: [ WARNING ] discarding 1 atoms at position 3 in file . Best match rsd_type:  CYS
core.io.pose_from_sfr.PoseFromSFRBuilder: [ WARNING ] discarding 1 atoms at position 4 in file . Best match rsd_type:  PRO
core.io.pose_from_sfr.PoseFromSFRBuilder: [ WARNING ] discarding 2 atoms at position 6 in file . Best match rsd_type:  MET
core.io.pose_from_sfr.PoseFromSFRBuilder: [ WARNING ] discarding 2 atoms at position 7 in file . Best match rsd_type:  ASP
core.io.pose_from_sfr.PoseFromSFRBuilder: [ WARNING ] discarding 1 atoms at position 8 in file . Best match rsd_type:  ILE
core.io.pose_from_sfr.PoseFromSFRBuilder: [ WARNING ] discarding 5 atoms at position 9 in fil

In [69]:
x_init, seq_init = sampler.sample_init()
designed_structure = run_sampler(sampler, x_init, seq_init)

core.io.pose_from_sfr.PoseFromSFRBuilder: [ WARNING ] discarding 4 atoms at position 1 in file . Best match rsd_type:  HIS:NtermProteinFull
core.io.pose_from_sfr.PoseFromSFRBuilder: [ WARNING ] discarding 2 atoms at position 2 in file . Best match rsd_type:  MET
core.io.pose_from_sfr.PoseFromSFRBuilder: [ WARNING ] discarding 1 atoms at position 3 in file . Best match rsd_type:  PRO
core.io.pose_from_sfr.PoseFromSFRBuilder: [ WARNING ] discarding 3 atoms at position 4 in file . Best match rsd_type:  GLU
core.io.pose_from_sfr.PoseFromSFRBuilder: [ WARNING ] discarding 3 atoms at position 5 in file . Best match rsd_type:  GLU
core.io.pose_from_sfr.PoseFromSFRBuilder: [ WARNING ] discarding 3 atoms at position 6 in file . Best match rsd_type:  GLU
core.io.pose_from_sfr.PoseFromSFRBuilder: [ WARNING ] discarding 3 atoms at position 7 in file . Best match rsd_type:  LYS
core.io.pose_from_sfr.PoseFromSFRBuilder: [ WARNING ] discarding 5 atoms at position 10 in file . Best match rsd_type:  AR

100%|█████████████████████████████████████████████████████████| 50/50 [02:31<00:00,  3.03s/it]


In [70]:
designed_pdb_str = protein.to_pdb(designed_structure)
show_pdb_string(designed_pdb_str)

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

## PPI

```bash
../scripts/run_inference.py 
inference.output_prefix=example_outputs/design_ppi 
inference.input_pdb=input_pdbs/insulin_target.pdb 
'contigmap.contigs=[A1-150/0 70-100]' 
'ppi.hotspot_res=[A59,A83,A91]' 
inference.num_designs=10 
denoiser.noise_scale_ca=0 
denoiser.noise_scale_frame=0
```

In [59]:
designer = RFDiffusionForUnconditionalStructureDesign(model_name="complex_base")

In [80]:
with open('insulin_target.pdb', mode="r") as f:
    pdb_str = f.read()

input_structure = protein.from_pdb_string(pdb_str, atom14_format=True, parse_hetatom=True)

In [61]:
sampler = SelfConditioning(
    model=designer.model,
    diffuser_conf=designer.cfg.diffuser,
    preprocess_conf=designer.cfg.preprocess,
    inference_conf=config.InferenceConfig(input_structure=input_structure, num_designs=1),
    contigmap_conf=config.ContigMap(contigs=["A1-150/0 70-100"]),
    symmetry_conf=config.SymmetryParams(),
    ppi_conf=config.PPIParams(hotspot_res=["A59", "A83", "A91"]),
    denoiser_conf=config.DenoiserParams(),
    potential_conf=config.PotentialsParams(),
)

Successful diffuser __init__


In [62]:
x_init, seq_init = sampler.sample_init()
designed_structure = run_sampler(sampler, x_init, seq_init)

With this beta schedule (linear schedule, beta_0 = 0.04, beta_T = 0.28), alpha_bar_T = 0.00013696050154976547


100%|█████████████████████████████████████████████████████████| 50/50 [02:06<00:00,  2.53s/it]


In [63]:
designed_pdb_str = protein.to_pdb(designed_structure)
show_pdb_string(designed_pdb_str)

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

### Beta model

In [82]:
designer = RFDiffusionForUnconditionalStructureDesign(model_name="complex_beta")

Downloading: "http://files.ipd.uw.edu/pub/RFdiffusion/f572d396fae9206628714fb2ce00f72e/Complex_beta_ckpt.pt" to /home/conradry71/.cache/torch/hub/checkpoints/complex_beta.pt
100%|██████████████████████████████████████████████████████| 461M/461M [00:07<00:00, 68.3MB/s]


In [83]:
sampler = SelfConditioning(
    model=designer.model,
    diffuser_conf=designer.cfg.diffuser,
    preprocess_conf=designer.cfg.preprocess,
    inference_conf=config.InferenceConfig(input_structure=input_structure, num_designs=1),
    contigmap_conf=config.ContigMap(contigs=["A1-150/0 70-100"]),
    symmetry_conf=config.SymmetryParams(),
    ppi_conf=config.PPIParams(hotspot_res=["A59", "A83", "A91"]),
    denoiser_conf=config.DenoiserParams(),
    potential_conf=config.PotentialsParams(),
)

Successful diffuser __init__


In [84]:
x_init, seq_init = sampler.sample_init()
designed_structure = run_sampler(sampler, x_init, seq_init)

With this beta schedule (linear schedule, beta_0 = 0.04, beta_T = 0.28), alpha_bar_T = 0.00013696050154976547


100%|█████████████████████████████████████████████████████████| 50/50 [02:14<00:00,  2.68s/it]


In [85]:
designed_pdb_str = protein.to_pdb(designed_structure)
show_pdb_string(designed_pdb_str)

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

## Tetrahedral Oligos

```bash
python ../scripts/run_inference.py 
--config-name=symmetry 
inference.symmetry="tetrahedral" 
inference.num_designs=10 
inference.output_prefix="example_outputs/tetrahedral_oligo" 
'potentials.guiding_potentials=["type:olig_contacts,weight_intra:1,weight_inter:0.1"]' 
potentials.olig_intra_all=True 
potentials.olig_inter_all=True 
potentials.guide_scale=2.0 
potentials.guide_decay="quadratic" 
'contigmap.contigs=[1200-1200]'
```

In [74]:
designer = RFDiffusionForUnconditionalStructureDesign(model_name="base")

In [75]:
with open('1qys.pdb', mode="r") as f:
    pdb_str = f.read()

input_structure = protein.from_pdb_string(pdb_str, atom14_format=True, parse_hetatom=True)

In [77]:
sampler = SelfConditioning(
    model=designer.model,
    diffuser_conf=designer.cfg.diffuser,
    preprocess_conf=designer.cfg.preprocess,
    inference_conf=config.InferenceConfig(input_structure=input_structure, num_designs=1),
    contigmap_conf=config.ContigMap(contigs=["600-600"]),
    symmetry_conf=config.SymmetryParams(symmetry="tetrahedral"),
    ppi_conf=config.PPIParams(),
    denoiser_conf=config.DenoiserParams(),
    potential_conf=config.PotentialsParams(
        guiding_potentials=["type:olig_contacts,weight_intra:1,weight_inter:0.1"],
        olig_inter_all=True,
        olig_intra_all=True,
        guide_scale=2,
        guide_decay="quadratic",
    ),
)

Successful diffuser __init__


In [78]:
x_init, seq_init = sampler.sample_init()
designed_structure = run_sampler(sampler, x_init, seq_init)

With this beta schedule (linear schedule, beta_0 = 0.04, beta_T = 0.28), alpha_bar_T = 0.00013696050154976547


100%|█████████████████████████████████████████████████████████| 50/50 [15:01<00:00, 18.03s/it]


In [79]:
designed_pdb_str = protein.to_pdb(designed_structure)
show_pdb_string(designed_pdb_str)

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

## TIM Barrel

```bash
../scripts/run_inference.py 
inference.output_prefix=example_outputs/design_tim_barrel 
scaffoldguided.scaffoldguided=True 
scaffoldguided.target_pdb=False 
scaffoldguided.scaffold_dir=tim_barrel_scaffold/ 
inference.num_designs=10 
denoiser.noise_scale_ca=0.5 
denoiser.noise_scale_frame=0.5 
scaffoldguided.sampled_insertion=0-5 
scaffoldguided.sampled_N=0-5 
scaffoldguided.sampled_C=0-5
```

In [134]:
designer = RFDiffusionForUnconditionalStructureDesign(model_name="complex_fold_base")

In [135]:
with open('1qys.pdb', mode="r") as f:
    pdb_str = f.read()
input_structure = protein.from_pdb_string(pdb_str, atom14_format=True, parse_hetatom=True)

with open('tim10.pdb', mode="r") as f:
    scaffold_pdb_str = f.read()

In [141]:
sampler = ScaffoldedSampler(
    model=designer.model,
    diffuser_conf=designer.cfg.diffuser,
    preprocess_conf=designer.cfg.preprocess,
    inference_conf=config.InferenceConfig(input_structure=input_structure, num_designs=1),
    contigmap_conf=config.ContigMap(),
    symmetry_conf=config.SymmetryParams(),
    ppi_conf=config.PPIParams(),
    denoiser_conf=config.DenoiserParams(noise_scale_ca=0.5, noise_scale_frame=0.5),
    potential_conf=config.PotentialsParams(),
    scaffold_conf=config.ScaffoldGuidedParams(
        target_pdb_str=None,
        target_adj=False,
        target_ss=False,
        scaffoldguided=True,
        scaffold_pdb_str_list=[scaffold_pdb_str],
        sampled_insertion="0-5",
        sampled_N="0-5",
        sampled_C="0-5",
    ),
)

In [142]:
x_init, seq_init = sampler.sample_init()
designed_structure = run_sampler(sampler, x_init, seq_init)

core.io.pose_from_sfr.PoseFromSFRBuilder: [ WARNING ] discarding 2 atoms at position 1 in file . Best match rsd_type:  ASP:NtermProteinFull
core.io.pose_from_sfr.PoseFromSFRBuilder: [ WARNING ] discarding 1 atoms at position 2 in file . Best match rsd_type:  ILE
core.io.pose_from_sfr.PoseFromSFRBuilder: [ WARNING ] discarding 2 atoms at position 3 in file . Best match rsd_type:  LEU
core.io.pose_from_sfr.PoseFromSFRBuilder: [ WARNING ] discarding 1 atoms at position 4 in file . Best match rsd_type:  ILE
core.io.pose_from_sfr.PoseFromSFRBuilder: [ WARNING ] discarding 1 atoms at position 5 in file . Best match rsd_type:  VAL
core.io.pose_from_sfr.PoseFromSFRBuilder: [ WARNING ] discarding 2 atoms at position 6 in file . Best match rsd_type:  ASP
core.io.pose_from_sfr.PoseFromSFRBuilder: [ WARNING ] discarding 2 atoms at position 8 in file . Best match rsd_type:  THR
core.io.pose_from_sfr.PoseFromSFRBuilder: [ WARNING ] discarding 2 atoms at position 9 in file . Best match rsd_type:  ASP

100%|█████████████████████████████████████████████████████████| 50/50 [02:05<00:00,  2.50s/it]


In [143]:
designed_pdb_str = protein.to_pdb(designed_structure)
show_pdb_string(designed_pdb_str)

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

## Unconditional with Contact Potential

```bash
../scripts/run_inference.py 
inference.output_prefix=example_outputs/design_unconditional_w_contact_potential 
'contigmap.contigs=[100-200]' 
inference.num_designs=10 
'potentials.guiding_potentials=["type:monomer_contacts,weight:0.05"]'
```

In [93]:
designer = RFDiffusionForUnconditionalStructureDesign(model_name="base")

In [94]:
with open('1qys.pdb', mode="r") as f:
    pdb_str = f.read()

input_structure = protein.from_pdb_string(pdb_str, atom14_format=True, parse_hetatom=True)

In [95]:
sampler = SelfConditioning(
    model=designer.model,
    diffuser_conf=designer.cfg.diffuser,
    preprocess_conf=designer.cfg.preprocess,
    inference_conf=config.InferenceConfig(input_structure=input_structure, num_designs=1),
    contigmap_conf=config.ContigMap(contigs=["100-200"]),
    symmetry_conf=config.SymmetryParams(),
    ppi_conf=config.PPIParams(),
    denoiser_conf=config.DenoiserParams(),
    potential_conf=config.PotentialsParams(guiding_potentials=["type:monomer_contacts,weight:0.05"]),
)

Successful diffuser __init__


In [96]:
x_init, seq_init = sampler.sample_init()
designed_structure = run_sampler(sampler, x_init, seq_init)

With this beta schedule (linear schedule, beta_0 = 0.04, beta_T = 0.28), alpha_bar_T = 0.00013696050154976547


100%|█████████████████████████████████████████████████████████| 50/50 [01:10<00:00,  1.41s/it]


In [97]:
designed_pdb_str = protein.to_pdb(designed_structure)
show_pdb_string(designed_pdb_str)

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

## Unconditional with Monomer ROG

```bash
../scripts/run_inference.py 
inference.output_prefix=example_outputs/design_monomer_ROG_unconditional 
'contigmap.contigs=[100-200]' 
inference.num_designs=10 
'potentials.guiding_potentials=["type:monomer_ROG,weight:1,min_dist:5"]' 
potentials.guide_scale=2 
potentials.guide_decay="quadratic"
```

In [98]:
designer = RFDiffusionForUnconditionalStructureDesign(model_name="base")

In [99]:
with open('1qys.pdb', mode="r") as f:
    pdb_str = f.read()

input_structure = protein.from_pdb_string(pdb_str, atom14_format=True, parse_hetatom=True)

In [100]:
sampler = SelfConditioning(
    model=designer.model,
    diffuser_conf=designer.cfg.diffuser,
    preprocess_conf=designer.cfg.preprocess,
    inference_conf=config.InferenceConfig(input_structure=input_structure, num_designs=1),
    contigmap_conf=config.ContigMap(contigs=["100-200"]),
    symmetry_conf=config.SymmetryParams(),
    ppi_conf=config.PPIParams(),
    denoiser_conf=config.DenoiserParams(),
    potential_conf=config.PotentialsParams(
        guiding_potentials=["type:monomer_ROG,weight:1,min_dist:5"],
        guide_scale=2,
        guide_decay="quadratic",
    ),
)

Successful diffuser __init__


In [101]:
x_init, seq_init = sampler.sample_init()
designed_structure = run_sampler(sampler, x_init, seq_init)

With this beta schedule (linear schedule, beta_0 = 0.04, beta_T = 0.28), alpha_bar_T = 0.00013696050154976547


100%|█████████████████████████████████████████████████████████| 50/50 [00:36<00:00,  1.36it/s]


In [102]:
designed_pdb_str = protein.to_pdb(designed_structure)
show_pdb_string(designed_pdb_str)

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

## Unconditional

```bash
../scripts/run_inference.py 
inference.output_prefix=example_outputs/design_unconditional 
'contigmap.contigs=[100-200]' 
inference.num_designs=10
```

In [103]:
designer = RFDiffusionForUnconditionalStructureDesign(model_name="base")

In [104]:
with open('1qys.pdb', mode="r") as f:
    pdb_str = f.read()

input_structure = protein.from_pdb_string(pdb_str, atom14_format=True, parse_hetatom=True)

In [108]:
sampler = SelfConditioning(
    model=designer.model,
    diffuser_conf=designer.cfg.diffuser,
    preprocess_conf=designer.cfg.preprocess,
    inference_conf=config.InferenceConfig(input_structure=input_structure, num_designs=1),
    contigmap_conf=config.ContigMap(contigs=["100-200"]),
    symmetry_conf=config.SymmetryParams(),
    ppi_conf=config.PPIParams(),
    denoiser_conf=config.DenoiserParams(),
    potential_conf=config.PotentialsParams(),
)

In [109]:
x_init, seq_init = sampler.sample_init()
designed_structure = run_sampler(sampler, x_init, seq_init)

100%|█████████████████████████████████████████████████████████| 50/50 [01:19<00:00,  1.60s/it]


In [107]:
designed_pdb_str = protein.to_pdb(designed_structure)
show_pdb_string(designed_pdb_str)

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

## Folding

In [139]:
from proteome import protein
from proteome.models.design.proteinmpnn.modeling import ProteinMPNNForSequenceDesign
from proteome.models.folding.omegafold.modeling import OmegaFoldForFolding

In [140]:
sequence_designer = ProteinMPNNForSequenceDesign("vanilla_model-20", random_seed=37)
folder = OmegaFoldForFolding()

In [143]:
target_structure = protein.from_pdb_string(designed_pdb, chain_id="A")
target_structure = protein.to_backbone_only_protein(target_structure)

In [144]:
sequence, score = sequence_designer.design_sequence(target_structure)
print(f"Sequence: {sequence} with global_score {score}")

Sequence: AALAAAAAALAAAHAAAHAAAAAALAALAAADPAAAAALGAAAAAAHAAAGAAHAAAAALAAAA with global_score 0.8552732467651367


In [151]:
predicted_protein, confidence = folder.fold(sequence)
folded_pdb = protein.to_pdb(predicted_protein)

In [152]:
PLDDT_BANDS = [
  (0, 50, '#FF7D45'),
  (50, 70, '#FFDB13'),
  (70, 90, '#65CBF3'),
  (90, 100, '#0053D6')
]
view = py3Dmol.view(width=800, height=600)
view.addModelsAsFrames(folded_pdb)

color_map = {i: bands[2] for i, bands in enumerate(PLDDT_BANDS)}
style = {'cartoon': {'colorscheme': {'prop': 'b', 'map': color_map}}}

style['stick'] = {}

view.setStyle({'model': -1}, style)
view.zoomTo()

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol